# Master TECR file creation

## Adding Elad_file lines to the master_file

### Define the requisite functions

In [3]:
# define the printing function
def set_contrast(data_description, master_set, set_1, set_1_description, set_2, set_2_description, verbose_printing = False, total_values = True):
    # print the original sets
    if total_values:
        print('\n{} in the master file: '.format(data_description), len(master_set))
        print('{} in the {} file: '.format(data_description, set_1_description), len(set_1))
        print('{} in the {} file: '.format(data_description, set_2_description), len(set_2))
    
    # contrast the sets
    extra_set_1 = master_set - set_1
    missing_set_1 = set_1 - master_set
    extra_set_2 = master_set - set_2
    missing_set_2 = set_2 - master_set
    if verbose_printing:
        print('\nExtra {} in the master file, versus {}: '.format(data_description, set_1_description), len(extra_set_1), '\n', extra_set_1)
        print('\nExtra {} in the master file, versus {}: '.format(data_description, set_2_description), len(extra_set_2), '\n', extra_set_2)
        print('\nMissing {} in the master file, versus {}: '.format(data_description, set_1_description), len(missing_set_1), '\n', missing_set_1)
        print('\nMissing {} in the master file, versus {}: '.format(data_description, set_2_description), len(missing_set_2), '\n', missing_set_2)
    else:
        print('\nExtra {} in the master file, versus {}: '.format(data_description, set_1_description), len(extra_set_1))
        print('Extra {} in the master file, versus {}: '.format(data_description, set_2_description), len(extra_set_2))
        print('Missing {} in the master file, versus {}: '.format(data_description, set_1_description), len(missing_set_1))
        print('Missing {} in the master file, versus {}: '.format(data_description, set_2_description), len(missing_set_2))
        
    return missing_set_1, missing_set_2


# add the units of logarithm to the Magnesium concentration
def isnumber(string):
    from numpy import nan
    
    if string is not nan and string not in ['', ' ', nan]:
        try:
            float(string)
            return True
        except:
            try:
                string.isnumeric()
                return True
            except:
                return False

### Merge the TECR scrapings

In [10]:
from datetime import date
from numpy import nan
import pandas
import re

empty = [nan, 'nan', None, ' ', '', 'NaN']

# import the spreadsheets
equilibrator_2008 = pandas.read_csv('TECRDB_Elad_Noor.csv')
equilibrator_2008 = equilibrator_2008.fillna(' ')

master_file = pandas.read_csv('2021-08-04_vetted & reorganized NIST database_01.csv')  # or '2021-08-04_vetted&reorganized_TECR.csv'
master_file = master_file.fillna(' ')

# establish standard IDs for each TECR datum
original_master_file_length = len(master_file)
column_nans = ['' for row in range(original_master_file_length)]
master_file.insert(0, 'standard_id', column_nans)

try:
    for column in equilibrator_2008:
        if re.search('Unnamed', column):
            del equilibrator_2008[column]
    standard_ids = [id for id in range(len(equilibrator_2008))]
    equilibrator_2008.insert(0, 'standard_id', standard_ids)
    equilibrator_2008.to_csv('TECRDB_Elad_Noor.csv')
except:
    pass

# parse Elad's spreadsheet with master spreadsheet
master_file.insert(2, 'KEGG Reaction:', column_nans)
display(master_file.head(5))

# contrast the enzymes
winter_enzyme_names = set(master_file['Enzyme:'])
striped_enzymes = set()
for enzyme in winter_enzyme_names:
    enzyme = enzyme.strip()
    striped_enzymes.add(enzyme)
    
equilibrator_enzyme_names = set(equilibrator_2008['enzyme_name'])  
missing_winter_enzymes, missing_equilibrator_enzymes = set_contrast('enzymes', striped_enzymes, striped_enzymes, 'Master file', equilibrator_enzyme_names, 'eQuilibrator 2008', verbose_printing = False)

# contrast the references   
equilibrator_references = set(equilibrator_2008['reference'])
master_references = set(master_file['Reference ID:'])
master_striped_references = set()
for reference in master_references:
    if reference not in [' ']:
        substituted_reference = re.sub('_.+', '', reference)
        master_striped_references.add(substituted_reference)
missing_winter_references, missing_equilibrator_references = set_contrast('references', master_striped_references, master_striped_references, 'Master file', equilibrator_references, 'eQuilibrator 2008', verbose_printing = False)

for elad_index, elad_row in equilibrator_2008.iterrows():
    elad_enzyme = elad_row['enzyme_name']
    elad_reference = elad_row['reference']
                 
    # add undescribed enzymes and citations
    if elad_reference in missing_equilibrator_references or elad_enzyme in missing_equilibrator_enzymes:
        # define the column values 
        add_id = elad_row['standard_id']
        add_enzyme = elad_row['enzyme_name']
        add_reference = elad_row['reference']
        add_method = elad_row['method']
        add_ec = elad_row['EC']
        add_kegg_reaction = elad_row['reaction']
        add_reaction = elad_row['description']
        add_pmg = elad_row['p_mg']
        add_k = elad_row['K_prime']
        if add_k is nan:
            add_k = elad_row['K']
        add_temperature = elad_row['temperature']
        add_ionic_strength = elad_row['ionic_strength']
        add_ph = elad_row['p_h']
        
        # add a new row at the end of master dataframe, according to master column organization
        master_file.loc[len(master_file.index)] = [add_id, add_enzyme, add_kegg_reaction, add_reaction, '', add_reference, add_temperature, add_ph, add_k, '', add_method, '', add_pmg, add_ec, '', '', '', add_ionic_strength, '']
       
undescribed = list(master_file['Experimental conditions'])[original_master_file_length + 1 :]
for row in undescribed:
    if isnumber(row):
        print(row)
        index = list(master_file['Experimental conditions']).index(row)
        master_file.at[index, 'Experimental conditions'] = '{} = -log[Mg+2]'.format(str(row))
        print(master_file.at[index, 'Experimental conditions'])
        
# strip spaces from the Pandas elements
for column in master_file:
    print(master_file[column])
    
    for index, entry in master_file[column].iteritems():
        if entry is float:
            master_file.at[index, column] = str(entry).strip(' ?~')
            master_file.at[index, column] = float(entry)
        elif entry is int:
            master_file.at[index, column] = str(entry).strip(' ?~')
            master_file.at[index, column] = int(entry)
        else:
            master_file.at[index, column] = str(entry).strip(' ?~')

# extrapolate metadata to all datums
for index, row in master_file.iterrows():    
    if row['Reference ID:'] not in empty:
        reference_id = row['Reference ID:']
        reference = row['Reference:']
        methods = row['Method:']
        buffer = row['Buffer:']
        ec = row['EC Value:']
    elif row['Reference ID:'] in empty:
        master_file.at[index, 'Reference ID:'] = reference_id
        master_file.at[index, 'Reference:'] = reference
        master_file.at[index, 'Method:'] = methods
        master_file.at[index, 'Buffer:'] = buffer
        master_file.at[index, 'EC Value:'] = ec
    else:
        print('ERROR: The reference has an unidentified structure.')

                
csv_name = '2021-08-16_master_TECR_1.csv'
master_file.to_csv(csv_name)

standard_id                   Enzyme: KEGG Reaction:  \
0               aspartate ammonia-lyase                  
1               aspartate ammonia-lyase                  
2                    fumarate hydratase                  
3                    fumarate hydratase                  
4                    fumarate hydratase                  

                                       Reaction:  \
0   L-aspartate(aq) = fumarate(aq) + ammonia(aq)   
1   L-aspartate(aq) = fumarate(aq) + ammonia(aq)   
2         fumarate(aq) + H2O(l) = (S)-malate(aq)   
3         fumarate(aq) + H2O(l) = (S)-malate(aq)   
4         fumarate(aq) + H2O(l) = (S)-malate(aq)   

                                          Reference:   Reference ID:   T [K]  \
0  Quastel J.H.; Woolf B.; Biochem. J.; 20 545 (1...  26QUA/WOO_1205  310.15   
1              Woolf B.; Biochem. J.; 23 472 (1929).      29WOO_1206  310.15   
2  Borsook H.; Schott H.F.; J. Biol. Chem.; 92 55...  31BOR/SCH_1141  298.15   
3                                                                     298.15   
4       Jacobsohn K.P.; Biochem. Z.; 274 167 (1934).      34JAC_1142  278.15   

    pH     Keq Km                             Method:     Buffer:  \
0   7.4  ~0.04                      chemical analysis   phosphate   
1   7.4   0.01      chemical analysis and polarimetry   phosphate   
2  6.81    3.1                       electrochemistry               
3  7.12    3.3                                                      
4   6.8    8.4                            polarimetry    barbital   

  Experimental conditions                                          EC Value:  \
0                           4.3.1.1\r                                    ...   
1                           4.3.1.1\r                                    ...   
2                           4.2.1.2\r                                    ...   
3                                                                              
4                           4.2.1.2\r                                    ...   

  solutes [mol / kg] solutes [mol / dm^3] Ionic strength [mol / dm^3]  \
0                                                                       
1                                                                       
2                                                                       
3                                                                       
4                                                                       

  Ionic strength [mol / kg] Enthalpy [kJ / mol]  
0                                                
1                                                
2                                                
3                                                
4


enzymes in the master file:  425
enzymes in the Master file file:  425
enzymes in the eQuilibrator 2008 file:  431

Extra enzymes in the master file, versus Master file:  0
Extra enzymes in the master file, versus eQuilibrator 2008:  61
Missing enzymes in the master file, versus Master file:  0
Missing enzymes in the master file, versus eQuilibrator 2008:  67

references in the master file:  911
references in the Master file file:  911
references in the eQuilibrator 2008 file:  919

Extra references in the master file, versus Master file:  0
Extra references in the master file, versus eQuilibrator 2008:  96
Missing references in the master file, versus Master file:  0
Missing references in the master file, versus eQuilibrator 2008:  104
1.0
1.0 = -log[Mg+2]
1.0
1.0 = -log[Mg+2]
1.0
1.0 = -log[Mg+2]
1.0
1.0 = -log[Mg+2]
1.0
1.0 = -log[Mg+2]
1.0
1.0 = -log[Mg+2]
1.0
1.0 = -log[Mg+2]
3.0
3.0 = -log[Mg+2]
2.3
2.3 = -log[Mg+2]
2.15
2.15 = -log[Mg+2]
2.0
2.0 = -log[Mg+2]
2.4
2.4 = -log[Mg+2

3.0 = -log[Mg+2]
2.7
2.7 = -log[Mg+2]
3.0
3.0 = -log[Mg+2]
3.0
3.0 = -log[Mg+2]
2.4
2.4 = -log[Mg+2]
1.7
1.7 = -log[Mg+2]
2.22
2.22 = -log[Mg+2]
2.0
2.0 = -log[Mg+2]
2.22
2.22 = -log[Mg+2]
1.7
1.7 = -log[Mg+2]
2.0
2.0 = -log[Mg+2]
2.7
2.7 = -log[Mg+2]
1.7
1.7 = -log[Mg+2]
3.0
3.0 = -log[Mg+2]
1.7
1.7 = -log[Mg+2]
2.7
2.7 = -log[Mg+2]
2.7
2.7 = -log[Mg+2]
1.7
1.7 = -log[Mg+2]
2.0
2.0 = -log[Mg+2]
2.7
2.7 = -log[Mg+2]
2.0
2.0 = -log[Mg+2]
2.0
2.0 = -log[Mg+2]
1.7
1.7 = -log[Mg+2]
2.7
2.7 = -log[Mg+2]
2.22
2.22 = -log[Mg+2]
2.22
2.22 = -log[Mg+2]
2.7
2.7 = -log[Mg+2]
2.22
2.22 = -log[Mg+2]
2.0
2.0 = -log[Mg+2]
2.0
2.0 = -log[Mg+2]
2.22
2.22 = -log[Mg+2]
1.74
1.74 = -log[Mg+2]
1.85
1.85 = -log[Mg+2]
2.7
2.7 = -log[Mg+2]
3.49
3.49 = -log[Mg+2]
3.18
3.18 = -log[Mg+2]
1.85
1.85 = -log[Mg+2]
2.52
2.52 = -log[Mg+2]
3.18
3.18 = -log[Mg+2]
2.4
2.4 = -log[Mg+2]
2.7
2.7 = -log[Mg+2]
2.22
2.22 = -log[Mg+2]
2.96
2.96 = -log[Mg+2]
2.22
2.22 = -log[Mg+2]
2.4
2.4 = -log[Mg+2]
2.96
2.96 = -log[Mg+2]
2.52

## Aligning Elad_file datum with master_file datum

### Define the requisite functions

In [9]:
# merging values between matched datum
def redefine_master(master_row, elad_row, master_id, elad_id):
    from numpy import unique
    empty = [nan, 'nan', None, ' ', '', 'NaN']
    
    # print the datum pair for manual inspection
    announcement = '\nmatched pair:'
    print(announcement, '\n', '='*len(announcement))
    print('elad_index', elad_index)
    print('master_index', master_index, '\n')
    
    # match KEGG reactions
    master_kegg = master_row['KEGG Reaction:']
    elad_kegg = elad_row['reaction']
    if master_kegg in empty:
        master_file.at[master_index, 'KEGG Reaction:'] = elad_kegg

    # match magnesium concentrations
    master_pmg = master_row['Experimental conditions']
    elad_pmg = elad_row['p_mg']
    if str(master_pmg) == '{} = -log[Mg+2]'.format(str(elad_pmg)):
        pass            
    elif elad_pmg not in empty and elad_pmg is not nan:
        if master_pmg is nan or master_pmg in empty:
            master_file.at[master_index, 'Experimental conditions'] = '{} = -log[Mg+2]'.format(str(elad_row['p_mg']))
            print(master_index, '\t', 'new pmg', '\t', master_file.at[master_index, 'Experimental conditions'])
        else:
            master_file.at[master_index, 'Experimental conditions'] = " or ".join([str(master_pmg), '{} (-log[Mg+2])'.format(str(elad_pmg))]) 
            print(master_index, '\t', 'new pmg', '\t', master_file.at[master_index, 'Experimental conditions'])            

    # match methods
    master_method = master_row['Method:']
    elad_method = elad_row['method']
    if master_method == elad_method:
        pass            
    elif master_method is nan or master_method  in empty:
        master_file.at[master_index, 'Method:'] = elad_method
    elif elad_method is not nan and elad_method not in empty:
        elad_methods = elad_method.split(' and ')
        master_methods = elad_method.split(' and ')
        combined_methods = set(elad_methods + master_methods)
        
        if combined_methods is not None:
            combined_methods_string = ' and '.join([method for method in combined_methods])
        else:
            combined_methods_string = ' and '.join([elad_method, master_method])
        
        master_file.at[master_index, 'Method:'] = combined_methods_string
        print(master_index, '\t', 'new method', '\t', master_file.at[master_index, 'Method:'])

    # match EC values
    master_ec = master_row['EC Value:']
    elad_ec = elad_row['EC']
    if master_ec is not nan and master_ec not in empty:
        master_ec = [master_ec]
        if master_ec[0] == elad_ec:
            master_file.at[master_index, 'EC Value:'] = master_ec[0]   
        elif elad_ec is not nan and elad_ec not in empty:
            if re.search('&', elad_ec):
                elad_ecs = elad_ec.split('&')
                #elad_ecs = [str(ec) for ec in elad_ecs]
                total_ecs = unique(elad_ecs + master_ec)
            else:
                total_ecs = [master_ec[0], elad_ec]
            master_file.at[master_index, 'EC Value:'] = " & ".join(total_ecs)
            print(master_index, '\t', 'new EC', '\t', master_file.at[master_index, 'EC Value:'])
    else:
        master_file.at[master_index, 'EC Value:'] = elad_ec

    # match ionic strength concentrations
    master_ionic_strength = master_row['Ionic strength [mol / dm^3]']
    elad_ionic_strength = elad_row['ionic_strength']
    if str(master_ionic_strength) == str(elad_ionic_strength):
        pass            
    elif master_ionic_strength is nan or master_ionic_strength  in empty:
        master_file.at[master_index, 'Ionic strength [mol / dm^3]'] = elad_ionic_strength
    elif elad_ionic_strength is not nan and elad_ionic_strength not in empty:
        master_file.at[master_index, 'Ionic strength [mol / dm^3]'] = " & ".join([str(master_ionic_strength), str(elad_ionic_strength)])
        print(master_index, '\t', 'new ionic strength', '\t', master_file.at[master_index, 'Ionic strength [mol / dm^3]'])

    # match the standard_id
    if master_id == elad_id:
        pass            
    elif master_id is nan or master_id in empty:
        master_file.at[master_index, 'standard_id'] = elad_id
    elif elad_id is not nan and elad_id not in empty:
        master_file.at[master_index, 'standard_id'] = " & ".join([str(master_id), str(elad_id)])
        print(master_index, '\t', 'new standard_id', '\t', master_file.at[master_index, 'standard_id'])
    
# homogenize the charge format    
def charge_format(master_reaction):                                
    print(master_reaction)
    remove_string = re.search('\w(\d\-)', master_reaction).group(1)
    print(remove_string)
    master_reaction = re.sub(remove_string, '-{}'.format(remove_string), master_reaction)
    print(master_reaction)
    return master_reaction, remove_string


### Aligning datum values

In [11]:
from numpy import nan, unique
from datetime import date
import pandas
import json
import re

empty = [nan, 'nan', None, ' ', '', 'NaN']

# import the spreadsheets
equilibrator_2008 = pandas.read_csv('TECRDB_Elad_Noor.csv')
equilibrator_2008 = equilibrator_2008.fillna('')

master_file = pandas.read_csv('2021-08-16_master_TECR_1.csv')
master_file = master_file.fillna('')
        
# clarify the columns 
for column in master_file:
    if re.search('Unnamed', column):
        del master_file[column]
        
for index, master_ec in master_file['EC Value:'].iteritems():
    if master_ec not in empty:  
        master_ec = re.search('([\d|\.|\-]+)', master_ec).group()
        master_file['EC Value:'].iloc[index] = master_ec

# ========================================================================================================================================================        

matched_master_indices = []
display_count = 0
unmatched_entries = 0
errors_dictionary = {}
for elad_index, elad_row in equilibrator_2008.iterrows():
    matched_datum = False
    print('\nelad_index', elad_index)
    
    # define the Elad values for this datum 
    elad_id = elad_row['standard_id']
    elad_enzyme = elad_row['enzyme_name']
    elad_reference = elad_row['reference']
    elad_method = elad_row['method']
    elad_ec = elad_row['EC']
    elad_kegg_reaction = elad_row['reaction']
    elad_reaction = elad_row['description']
    elad_pmg = elad_row['p_mg']
    elad_k = elad_row['K_prime']
    if elad_k is nan:
        elad_k = elad_row['K']
    elad_temperature = elad_row['temperature']
    elad_ionic_strength = elad_row['ionic_strength']
    elad_ph = elad_row['p_h']
    
    # determine the set of possible matches
    matching_master_subset = master_file.loc[(master_file['Enzyme:'] == elad_enzyme)]    #  & (master_file['Keq'] == elad_k) & (master_file['T [K]'] == elad_temperature) & (master_file['pH '] == elad_ph)
    if display_count < 5:
        display(matching_master_subset)
    display_count += 1
    
    errors = []
    for master_index, master_row in matching_master_subset.iterrows():  
        # remove previously matched rows
        if master_index in matched_master_indices:
            error = ''.join([str(x) for x in [master_index, '\t','previously matched datum', '\t', elad_index]])
            errors.append(error)
            continue

        # define the master values for this datum 
        master_reference = master_row['Reference:']
        master_method = master_row['Method:']
        master_ec = master_row['EC Value:']
        master_pmg = master_row['Experimental conditions']
        master_ionic_strength = master_row['Ionic strength [mol / dm^3]']
        master_temperature = master_row['T [K]']
        master_ph = master_row['pH ']
        master_k = master_row['Keq']
        master_km = master_row['Km']
        
        master_id = master_row['standard_id']
        master_reference_id = re.sub('_.+', '', master_row['Reference ID:'])
        
        master_reaction = master_row['Reaction:']
        master_reaction = re.sub('\u00ce\u00b1|\u00ce\u00b2', '', master_reaction)
        master_reaction = re.sub('\u00cf\u2030', '-w', master_reaction)

        # match the reference
        if elad_reference != master_reference_id:
            error = ''.join([str(x) for x in [master_index, '\t', 'reference', '\t', elad_reference, '\t', master_reference_id]])
            print(error)
            errors.append(error)
            continue

        # match the reactions 
        if elad_reaction != master_reaction:
            if re.search('= -\w', master_reaction):
                remove_string = re.search('=(\s-)\w', master_reaction).group(1)
                master_reaction = re.sub(remove_string, '-', master_reaction)
            if elad_reaction != master_reaction:

                if re.search(' -D-', master_reaction):
                    remove_string = re.search('\s(-D-)', master_reaction).group(1)
                    master_reaction = re.sub(remove_string, 'D-', master_reaction, 1)
                if elad_reaction != master_reaction:

                    if re.search('\w\d\-', master_reaction):
                        loop = True
                        try:
                            while loop :
                                master_reaction, remove_string = charge_format(master_reaction)
                                if remove_string is None:
                                    loop = False
                        except:
                            pass
                    if elad_reaction != master_reaction:

                        if re.search('\(\w\)\-', master_reaction):
                            master_reaction = re.sub('\(\w\)\-', '', master_reaction)
                        if elad_reaction != master_reaction:

                            if re.search('-lipoate', master_reaction):
                                master_reaction = re.sub('(-lipoate)', 'lipoate', master_reaction, 1)
                            if elad_reaction != master_reaction:

                                error = ''.join([str(x) for x in [master_index, '\t', 'reaction', '\t', elad_reaction, '\t', master_reaction]])
                                print(error)
                                errors.append(error)
                                continue

        # match the temperature
        if (elad_temperature and master_temperature) is not nan and (elad_temperature and master_temperature) not in empty:
            if float(elad_temperature) != float(master_temperature):
                error = ''.join([str(x) for x in [master_index, '\t','temperature', '\t', elad_temperature, '\t', master_temperature]])
                print(error)
                errors.append(error)
                continue

        # match the pH
        if (elad_ph and master_ph) is not nan and (elad_ph and master_ph) not in empty:
            elad_ph = str(elad_ph).strip('?~')
            master_ph = str(master_ph).strip('?~')
            if float(elad_ph) != float(master_ph):
                error = ''.join([str(x) for x in [master_index, '\t','ph', '\t', elad_ph, '\t', master_ph]])
                print(error)
                errors.append(error)
                continue

        # match the Keq
        if re.search('\w(\?\w+)', str(master_k)):
            master_k = re.sub('(\?\w+)', '', str(master_k))

        if (elad_k and master_k) is not nan and (elad_k and master_k) not in empty:
            elad_k = float(str(elad_k).strip('~?'))
            master_k = float(str(master_k).strip('~?'))
            if float(elad_k) != float(master_k):
                error = ''.join([str(x) for x in [master_index, '\t', 'Keq', '\t', elad_k, '\t', master_k]])
                print(error)
                errors.append(error)
                continue

        # define the new data of the master file
        matched_datum = True
        redefine_master(master_row, elad_row, master_id, elad_id)
        break

    if not matched_datum:
        print('--> Failed index to match: ', elad_index, '\t', elad_enzyme)
        unmatched_entries += 1
        errors_dictionary[elad_index] = errors
    else:
        matched_master_indices.append(master_index)
        
# test for standard_id uniqueness and unmatched values
print('\nCompletely unique standard_ids: ', len(matched_master_indices) == len(set(matched_master_indices)))
print('Unmatched standard_ids: ', unmatched_entries)

# consolidate the solutes column 
for index, solute in master_file['solutes [mol / dm^3]'].iteritems():
    if solute is not nan and solute not in empty:  
        solute_list = solute.split(' & ')
        if len(solute_list) > 1:
            solute_list = unique(solute_list)
            if len(solute_list) > 2:
                print('Large solute set {}'.format(solute_list))
            else:
                master_file['solutes [mol / dm^3]'].iloc[index] = ' & '.join([x for x in list(solute_list)])

        elif solute_list[0] in ['#NAME']:
            master_file['solutes [mol / dm^3]'].iloc[index] = ''
        
# export the unmatched datums
with open('2021-08-12_unmatched_TECR_datums.json', 'w') as output:
    json.dump(errors_dictionary, output, indent = 3)

        
# export the combined master file
csv_name = '2021-08-16_master_TECR_2.csv'
master_file.to_csv(csv_name)


elad_index 0


standard_id                       Enzyme:  \
4041         0.0  homoisocitrate dehydrogenase   

                                         KEGG Reaction:  \
4041  kegg:C05662 + kegg:C00003 = kegg:C00322 + kegg...   

                                              Reaction: Reference:  \
4041  (1R,2S)-1-hydroxybutane-1,2,4-tricarboxylate(a...              

     Reference ID:   T [K]  pH    Keq Km            Method: Buffer:  \
4041     07LIN/ALG  298.15  7.5  0.45     spectrophotometry           

     Experimental conditions EC Value: solutes [mol / kg]  \
4041                          1.1.1.87                      

     solutes [mol / dm^3] Ionic strength [mol / dm^3]  \
4041                                                    

     Ionic strength [mol / kg] Enthalpy [kJ / mol]  
4041


matched pair: 
elad_index 0
master_index 4041 


elad_index 1


standard_id                                  Enzyme: KEGG Reaction:  \
1113              methenyltetrahydrofolate cyclohydrolase                  
1114              methenyltetrahydrofolate cyclohydrolase                  
1115              methenyltetrahydrofolate cyclohydrolase                  
1116              methenyltetrahydrofolate cyclohydrolase                  
1117              methenyltetrahydrofolate cyclohydrolase                  
1118              methenyltetrahydrofolate cyclohydrolase                  
1249              methenyltetrahydrofolate cyclohydrolase                  
1534              methenyltetrahydrofolate cyclohydrolase                  
2130              methenyltetrahydrofolate cyclohydrolase                  

                                              Reaction:  \
1113  5,10-methenyltetrahydrofolate(aq) + H2O(l) = 1...   
1114  5,10-methenyltetrahydrofolate(aq) + H2O(l) = 1...   
1115  5,10-methenyltetrahydrofolate(aq) + H2O(l) = 1...   
1116  5,10-methenyltetrahydrofolate(aq) + H2O(l) = 1...   
1117  5,10-methenyltetrahydrofolate(aq) + H2O(l) = 1...   
1118  5,10-methenyltetrahydrofolate(aq) + H2O(l) = 1...   
1249  5,10-methenyltetrahydrofolate(aq) + H2O(l) = 1...   
1534  5,10-methenyltetrahydrofolate(aq) + H2O(l) = 1...   
2130  5,10-methenyltetrahydrofolate(aq) + H2O(l) = 1...   

                                             Reference:   Reference ID:  \
1113  Kay L.D.; Osborn M.J.; Hatefi I.; Huennekens F...  60KAY/OSB_1057   
1114  Kay L.D.; Osborn M.J.; Hatefi I.; Huennekens F...  60KAY/OSB_1057   
1115  Kay L.D.; Osborn M.J.; Hatefi I.; Huennekens F...  60KAY/OSB_1057   
1116  Kay L.D.; Osborn M.J.; Hatefi I.; Huennekens F...  60KAY/OSB_1057   
1117  Kay L.D.; Osborn M.J.; Hatefi I.; Huennekens F...  60KAY/OSB_1057   
1118  Kay L.D.; Osborn M.J.; Hatefi I.; Huennekens F...  60KAY/OSB_1057   
1249    Greenberg D.M.; Methods Enzymol.; 6 386 (1963).      63GRE_1058   
1534  Lombrozo L.; Greenberg D.M.; Arch. Biochem. Bi...  67LOM/GRE_1059   
2130  Suzuki N.; Iwai K.; Plant Cell Physiol.; 14 31...  73SUZ/IWA_1060   

       T [K]   pH      Keq Km            Method:  \
1113  298.15  4.74  0.0733     spectrophotometry   
1114  298.15  5.20   0.127     spectrophotometry   
1115  298.15  5.20   0.221     spectrophotometry   
1116  298.15  5.70   0.818     spectrophotometry   
1117  298.15  7.00      11     spectrophotometry   
1118  298.15  7.13    12.7     spectrophotometry   
1249  298.15  6.50     4.2     spectrophotometry   
1534  298.15  6.50    1.84     spectrophotometry   
2130  298.15  7.00      50     spectrophotometry   

                                Buffer: Experimental conditions EC Value:  \
1113      citrate phosphate and acetate                           3.5.4.9   
1114      citrate phosphate and acetate                           3.5.4.9   
1115      citrate phosphate and acetate                           3.5.4.9   
1116      citrate phosphate and acetate                           3.5.4.9   
1117      citrate phosphate and acetate                           3.5.4.9   
1118      citrate phosphate and acetate                           3.5.4.9   
1249   potassium maleate (1.0 mol dm-3)                           3.5.4.9   
1534  potassium citrate (0.11 mol dm-3)                           3.5.4.9   
2130                  potassium maleate                           3.5.4.9   

     solutes [mol / kg] solutes [mol / dm^3] Ionic strength [mol / dm^3]  \
1113                                                                       
1114                                                                       
1115                                                                       
1116                                                                       
1117                                                                       
1118                                                                       
1249                                                                       
15

1113	reference	63GRE	60KAY/OSB
1114	reference	63GRE	60KAY/OSB
1115	reference	63GRE	60KAY/OSB
1116	reference	63GRE	60KAY/OSB
1117	reference	63GRE	60KAY/OSB
1118	reference	63GRE	60KAY/OSB

matched pair: 
elad_index 1
master_index 1249 


elad_index 2


...

3361	reference	93LAR/TEW	87ANT
3552	reference	93LAR/TEW	89ROM/DEM
3553	reference	93LAR/TEW	89ROM/DEM
3556	reference	93LAR/TEW	89ROM/DEM
3557	reference	93LAR/TEW	89ROM/DEM
3558	reference	93LAR/TEW	89ROM/DEM
3559	reference	93LAR/TEW	89ROM/DEM
3560	reference	93LAR/TEW	89ROM/DEM

matched pair: 
elad_index 4314
master_index 3777 

3777 	 new pmg 	 3.0 = -log[Mg+2]

elad_index 4315

matched pair: 
elad_index 4315
master_index 4908 


elad_index 4316

matched pair: 
elad_index 4316
master_index 1305 


elad_index 4317
2768	reference	98DIE/STR	80SVE/MAR
2769	reference	98DIE/STR	80SVE/MAR
2770	reference	98DIE/STR	80SVE/MAR
2771	reference	98DIE/STR	80SVE/MAR
2775	reference	98DIE/STR	80SVE/MAR
2776	reference	98DIE/STR	80SVE/MAR
3378	reference	98DIE/STR	87REK/EGO
3997	ph	5.6	5.0

matched pair: 
elad_index 4317
master_index 3998 


elad_index 4318
2768	reference	98DIE/STR	80SVE/MAR
2769	reference	98DIE/STR	80SVE/MAR
2770	reference	98DIE/STR	80SVE/MAR
2771	reference	98DIE/STR	80SVE/MAR
2775	referenc

178	reference	53BUR/WIL	38SCH/HEL
179	reference	53BUR/WIL	38SCH/HEL
180	reference	53BUR/WIL	38SCH/HEL
181	reference	53BUR/WIL	38SCH/HEL
182	reference	53BUR/WIL	38SCH/HEL
183	reference	53BUR/WIL	38SCH/HEL
184	reference	53BUR/WIL	38SCH/HEL
483	ph	7.52	7.03
484	ph	7.52	7.18
485	ph	7.52	7.28
486	ph	7.52	7.28
487	ph	7.52	7.28
488	ph	7.52	7.3
489	ph	7.52	7.51

matched pair: 
elad_index 4353
master_index 492 


elad_index 4354
178	reference	53BUR/WIL	38SCH/HEL
179	reference	53BUR/WIL	38SCH/HEL
180	reference	53BUR/WIL	38SCH/HEL
181	reference	53BUR/WIL	38SCH/HEL
182	reference	53BUR/WIL	38SCH/HEL
183	reference	53BUR/WIL	38SCH/HEL
184	reference	53BUR/WIL	38SCH/HEL
483	ph	7.68	7.03
484	ph	7.68	7.18
485	ph	7.68	7.28
486	ph	7.68	7.28
487	ph	7.68	7.28
488	ph	7.68	7.3
489	ph	7.68	7.51
495	ph	7.68	7.56
496	ph	7.68	7.63
499	ph	7.68	7.64
501	Keq	0.337	0.33

matched pair: 
elad_index 4354
master_index 502 


elad_index 4355
178	reference	53BUR/WIL	38SCH/HEL
179	reference	53BUR/WIL	38SCH/HEL
180	reference	

1966	Keq	0.33	0.13
1967	Keq	0.33	0.17

matched pair: 
elad_index 4392
master_index 1970 

1970 	 new pmg 	 2.4 = -log[Mg+2]

elad_index 4393
1966	Keq	0.17	0.13

matched pair: 
elad_index 4393
master_index 1967 

1967 	 new pmg 	 3.4 = -log[Mg+2]

elad_index 4394

matched pair: 
elad_index 4394
master_index 1966 

1966 	 new pmg 	 3.7 = -log[Mg+2]

elad_index 4395

matched pair: 
elad_index 4395
master_index 185 


elad_index 4396
619	reaction	ATP(aq) + propanoate(aq) + CoA(aq) = AMP(aq) + diphosphate(aq) + propanonyl-CoA(aq)	ATP(aq) + acetate(aq) + CoA(aq) = AMP(aq) + diphosphate(aq) + acetyl-CoA(aq)
620	reaction	ATP(aq) + propanoate(aq) + CoA(aq) = AMP(aq) + diphosphate(aq) + propanonyl-CoA(aq)	ATP(aq) + acetate(aq) + CoA(aq) = AMP(aq) + diphosphate(aq) + acetyl-CoA(aq)
621	reaction	ATP(aq) + propanoate(aq) + CoA(aq) = AMP(aq) + diphosphate(aq) + propanonyl-CoA(aq)	ATP(aq) + acetate(aq) + CoA(aq) = AMP(aq) + diphosphate(aq) + acetyl-CoA(aq)

matched pair: 
elad_index 4396
master_index

master_index 2805 


elad_index 4442
2809	ph	7.12	7.0
2810	ph	7.12	7.0
2813	ph	7.12	7.03
2814	Keq	2.61e-06	2.83e-06

matched pair: 
elad_index 4442
master_index 2815 

2815 	 new pmg 	 1.7 = -log[Mg+2]

elad_index 4443
2809	Keq	3.14e-06	2.57e-06

matched pair: 
elad_index 4443
master_index 2810 


elad_index 4444
2809	ph	7.12	7.0
2813	ph	7.12	7.03

matched pair: 
elad_index 4444
master_index 2814 

2814 	 new pmg 	 2.3 = -log[Mg+2]

elad_index 4445
2809	ph	7.54	7.0
2813	ph	7.54	7.03
2817	ph	7.54	7.53

matched pair: 
elad_index 4445
master_index 2818 


elad_index 4446
2809	ph	7.03	7.0

matched pair: 
elad_index 4446
master_index 2813 


elad_index 4447
2809	ph	7.53	7.0

matched pair: 
elad_index 4447
master_index 2817 


elad_index 4448

matched pair: 
elad_index 4448
master_index 2809 


elad_index 4449
249	reference	49MEY/GRE	45OHL
250	reference	49MEY/GRE	46OHL
251	reference	49MEY/GRE	46OHL
252	reference	49MEY/GRE	46OHL
253	reference	49MEY/GRE	46OHL

matched pair: 
elad_index 4449
ma


matched pair: 
elad_index 4510
master_index 4013 


elad_index 4511
655	ph	5.7	4.4

matched pair: 
elad_index 4511
master_index 656 


elad_index 4512

matched pair: 
elad_index 4512
master_index 655 


elad_index 4513

matched pair: 
elad_index 4513
master_index 412 


elad_index 4514

matched pair: 
elad_index 4514
master_index 1819 


elad_index 4515

matched pair: 
elad_index 4515
master_index 691 


elad_index 4516

matched pair: 
elad_index 4516
master_index 382 


elad_index 4517
1452	reference	85MAK/KIE	67DAN/YOS
1453	reference	85MAK/KIE	67DAN/YOS

matched pair: 
elad_index 4517
master_index 3222 


elad_index 4518
1452	reference	85MAK/KIE	67DAN/YOS
1453	reference	85MAK/KIE	67DAN/YOS
3223	Keq	1.107	1.109

matched pair: 
elad_index 4518
master_index 3224 


elad_index 4519
1452	reference	85MAK/KIE	67DAN/YOS
1453	reference	85MAK/KIE	67DAN/YOS
3223	Keq	1.114	1.109

matched pair: 
elad_index 4519
master_index 3225 


elad_index 4520
1452	reference	85MAK/KIE	67DAN/YOS
1453	referenc

# Programmatically adding the manual curation

The unmatched entitites datums in the '2021-08-12_unmatched_TECR_datums.json' file from the previous code was manually curated. The manual curation was guided by the near misses of matches that were identified in the aforementioned JSON file. Slight heterogeneities in reaction strings, which were difficult to programmatically catch and correct, were a common source of missing a match. The manual curation was recorded and briefly explained in the 'Manual curation of the programmatically unmatched datums.txt' file, which utilizes comma delimiters for programmability and tabs for readability.

In [13]:
import re

# import the files
manual_curation = pandas.read_csv('Manual curation of the programmatically unmatched datums, comma delimited.txt', header = 0)
master_file = pandas.read_csv('2021-08-16_master_TECR_2.csv')
master_file = master_file.fillna('')
for column in master_file:
    if re.search('Unnamed', column):
        del master_file[column]

# remove tabs from the dataframe
headings = []
for column in manual_curation:
    headings.append(column.strip('\t'))
    for index, row in manual_curation[column].iteritems():
        manual_curation[column].iloc[index] = row.strip('\t')
        
manual_curation.columns = headings
display(manual_curation)

# parse the manually curated content
parsing_errors = []
for index, row in manual_curation.iterrows():
    
    # characterize the curated datums            
    master_file_ids = [row['Master file index']]
    add = False
    if re.search('New', master_file_ids[0]):
        add = True
        
    merge = False
    if not re.search('--', master_file_ids[0]) and not add:            
        merge = True
        # parse the corresponding master_file indices
        if re.search('-', master_file_ids[0]):
            master_file_ids = master_file_ids[0].split('-')
            lower = int(master_file_ids[0])
            upper = int(master_file_ids[1])

            if lower < upper:
                id_range = upper - lower
                master_file_ids = [id + lower for id in range(id_range + 1)]                
            
        elif re.search(r'\\', master_file_ids[0]):
            master_file_ids = master_file_ids[0].split('\\')   
        else:
            master_file_ids = [int(master_file_ids[0])]
                
    # parse the previously unmatched standard IDs
    standard_ids = [row['standard ID']]
    if re.search('-', standard_ids[0]):
        standard_ids = standard_ids[0].split('-')
        lower = int(standard_ids[0])
        upper = int(standard_ids[1])

        if lower < upper:
            id_range = upper - lower
            standard_ids = [id + lower for id in range(id_range + 1)]
       
    else:
        standard_ids = [int(standard_ids[0])]
            
    # add new datums to the master file
    print(standard_ids)
    print(master_file_ids)
    if add or merge:
        for standard_id_index in range(len(standard_ids)):
            standard_id = standard_ids[standard_id_index]
            print(standard_id)
            elad_row = equilibrator_2008.iloc[int(standard_id)]
            elad_index = elad_row['standard_id']
                        
            if add:
                # define the datum values to add
                add_id = elad_row['standard_id']
                add_enzyme = elad_row['enzyme_name']
                add_reference = elad_row['reference']
                add_method = elad_row['method']
                add_ec = elad_row['EC']
                add_kegg_reaction = elad_row['reaction']
                add_reaction = elad_row['description']
                add_pmg = elad_row['p_mg']
                add_k = elad_row['K_prime']
                if add_k is nan:
                    add_k = elad_row['K']
                add_temperature = elad_row['temperature']
                add_ionic_strength = elad_row['ionic_strength']
                add_ph = elad_row['p_h']
                
                # elad a new row at the end of master dataframe, according to master column organization
                master_file.loc[len(master_file.index)] = [add_id, add_enzyme, add_kegg_reaction, add_reaction, '', add_reference, add_temperature, add_ph, add_k, '', add_method, '', add_pmg, add_ec, '', '', '', add_ionic_strength, '']

            if merge:
                # match the standard id with the master_index
                match_index = standard_ids.index(standard_id)
                master_index = master_file_ids[match_index]
                master_row = master_file.iloc[int(master_index)]

                # merge the content of the equilibrator_2008 and master_file for the corresponding standard id
                redefine_master(master_row, elad_row, master_id = None, elad_id = elad_index)
                
    else:
        # characterize the curated datums            
        error = row['Error resolution']
        if re.search('Duplicate', error):
            print('The {} standard ID is a duplicate.'.format(standard_ids))
        elif re.search('already', error):
            print('The {} standard ID is already matched.'.format(standard_ids))
        else:
            parsing_errors.append(standard_ids)
            print('ERROR: The {} standard ID was not captured by the parsing.'.format(standard_ids))

if parsing_errors == []:
    parsing_errors = None
print('Parsing errors: ', parsing_errors)
            
# export the expanded master_file
display(master_file.tail(5))
csv_name = '2021-08-16_master_TECR_3.csv'
master_file.to_csv(csv_name)

standard ID           Error resolution Master file index
0           38            Duplicate of 37                --
1           77           Duplicate of 269                --
2        79-80       Chemical name change           708-709
3          114           Duplicate of 113                --
4          270  Proton omission\inclusion              1762
..         ...                        ...               ...
71        4170       already matched 4868                --
72        4191          Duplicate of 4191                --
73        4367          Duplicate of 4366                --
74        4467                        New               New
75        4493          Duplicate of 4492                --

[76 rows x 3 columns]

[38]
['--']
The [38] standard ID is a duplicate.
[77]
['--']
The [77] standard ID is a duplicate.
[79, 80]
[708, 709]
79

matched pair: 
elad_index 79
master_index 708 

80

matched pair: 
elad_index 80
master_index 709 

[114]
['--']
The [114] standard ID is a duplicate.
[270]
[1762]
270

matched pair: 
elad_index 270
master_index 1762 

[271]
[1763]
271

matched pair: 
elad_index 271
master_index 1763 

[283]
[2009]
283

matched pair: 
elad_index 283
master_index 2009 

[315]
['--']
The [315] standard ID is a duplicate.
[358]
[' \t\t--']
The [358] standard ID is a duplicate.
[449]
[' \t\t--']
The [449] standard ID is a duplicate.
[470]
['--']
The [470] standard ID is a duplicate.
[518]
[1835]
518

matched pair: 
elad_index 518
master_index 1835 

[674]
['--']
The [674] standard ID is a duplicate.
[729]
[2281]
729

matched pair: 
elad_index 729
master_index 2281 

[849, 850]
[3577, 3578]
849

matched pair: 
elad_index 849
master_index 3577 

3577 	 new EC 	 3.2.1.21 & 3.2.1.20
850

ma

standard_id               Enzyme:  \
5151        3975  alkaline phosphatase   
5152        3976  alkaline phosphatase   
5153        3977  alkaline phosphatase   
5154        3978  alkaline phosphatase   
5155        4467   aconitate hydratase   

                                 KEGG Reaction:  \
5151  kegg:C00013 + kegg:C00001 = 2 kegg:C00009   
5152  kegg:C00013 + kegg:C00001 = 2 kegg:C00009   
5153  kegg:C00013 + kegg:C00001 = 2 kegg:C00009   
5154  kegg:C00013 + kegg:C00001 = 2 kegg:C00009   
5155    kegg:C00311 = kegg:C00417 + kegg:C00001   

                                              Reaction: Reference:  \
5151  pyrophosphate(aq) + H2O(l) = 2 orthophosphate(aq)              
5152  pyrophosphate(aq) + H2O(l) = 2 orthophosphate(aq)              
5153  pyrophosphate(aq) + H2O(l) = 2 orthophosphate(aq)              
5154  pyrophosphate(aq) + H2O(l) = 2 orthophosphate(aq)              
5155        isocitrate(aq) = cis-aconitate(aq) + H2O(l)              

     Reference ID:   T [K]  pH      Keq Km                           Method:  \
5151     89ROM/DEM  308.15  7.0  490.00     chromatography and radioactivity   
5152     89ROM/DEM  308.15  7.8  184.00     chromatography and radioactivity   
5153     89ROM/DEM  308.15  7.8  100.00     chromatography and radioactivity   
5154     89ROM/DEM  308.15  7.8  100.00     chromatography and radioactivity   
5155     43KRE/EGG  311.15  7.4    0.69                          polarimetry   

     Buffer: Experimental conditions EC Value: solutes [mol / kg]  \
5151                            2.38   3.1.3.1                      
5152                            2.00   3.1.3.1                      
5153                            1.30   3.1.3.1                      
5154                            1.30   3.1.3.1                      
5155                                   4.2.1.3                      

     solutes [mol / dm^3] Ionic strength [mol / dm^3]  \
5151                                                    
5152                                                    
5153                                                    
5154                                                    
5155                                                    

     Ionic strength [mol / kg] Enthalpy [kJ / mol]  
5151                                                
5152                                                
5153                                                
5154                                                
5155